In [1]:
import random
import string
import copy

class Building():
    def __init__(self, num_of_floor, num_of_passenger):
        self.num_of_floor = num_of_floor
        self.num_of_passenger = num_of_passenger
        self.passengers = [] #list of all passengers
        self.random_passengers()   # generate random passengers

    def random_passengers(self):
        for i in range(self.num_of_passenger):
            p = Passenger(random.randrange(self.num_of_floor), random.randrange(self.num_of_floor)) #generates an origin and a destination

            # make sure the origin and destination is different
            while p.origin == p.destination:
                p.destination = random.randrange(self.num_of_floor)

            self.passengers.append(p) #add random passenger to building

###########################################################################

class Passenger():
    def __init__(self, origin, destination):
        self.name = "".join(random.choice(string.ascii_uppercase)) +\
                    "".join(random.choice(string.ascii_lowercase) for _ in range(random.randrange(2, 8)))
                    # a random name for the passenger for console display
        self.origin = origin
        self.destination = destination
        self.deliver = 0   # marker of if the passenger is delivered, 0=undelivered 1=delivered
        self.cost = 0   # the cost to deliver the passenger

    def compute_cost(self, movement):
        self.cost = movement - abs(self.origin - self.destination)
        print("Drop off", self.name, "at floor", self.destination, "with cost", self.cost)

###########################################################################

class Elevator():
    def __init__(self, capacity, position=0, direction=1):
        self.capacity = capacity   # max allowed people in the elevator
        self.position = position   # current position of the elevator, defalut to 0
        self.movement = 0   # count the total movement of the elevator, used to calculate cost function
        self.direction = direction   # last moving direction of the elevator, 0=down 1=up, default to 1
        self.carrying = []   # a collection of passengers currently inside the elevator

    def move(self):
        # move one floor following the given direction
        if self.direction == 1:
            self.position += 1
        else:
            self.position -= 1

        self.movement += 1   # increment the total movement by 1 as the elevator has moved one more step

    def drop_passenger(self):
        # go through all passengers on the elevator to check if they reached their destination
        dropped = []
        for key, object in enumerate(self.carrying):
            if object.destination == self.position: #mark if passenger is at destination floor
                dropped.append(key) #add passenger to be dropped
                object.compute_cost(self.movement)
        
        if dropped: #removed dropped passengers from elevator
            self.carrying = [p for ind, p in enumerate(self.carrying) if ind not in dropped]


    def reverse(self):
        if self.direction == 1:
            self.direction = 0
        else:
            self.direction = 1

###########################################################################


# Strategy 1 has 3 principles:
# 1. The elevator will always favour its current moving direction.
# 2. Unless reached its capacity, the elevator will take all encountered passengers that are going in the same direction.
# 3. The elevator will reverse its current moving direction if:
#    1. There is no passenger currently inside the elevator.
#    2. There is no undelivered passenger in the elevator's current direction

def strategy_1(b, e): #inputs a building and an elevator
    awaiting = copy.copy(b.passengers) #list of passengers in the building 
    e.carrying = [] #reset elevator
    while len(awaiting) > 0 or len(e.carrying) > 0: #while there are people to be picked up or people to deliver
        print("The elevator is at", e.position, "carrying", len(e.carrying), "passengers")

        # at each floor, first check if there is a passenger to drop
        e.drop_passenger()

        # if the elevator still has capacity, check if there is passenger to carry
        if len(awaiting) > 0 and len(e.carrying) < e.capacity:
            DEL = []
            for key, object in enumerate(awaiting): #loop through all waiting passengers in the building
                if e.position == object.origin:
                    if ((object.destination - object.origin) > 0) == e.direction:   # if the elevator is going in the direction the passenger wants to go
                        e.carrying.append(object) #pick up passenger
                        DEL.append(key) # add passenger to be removed from elevator calls
                        print("Picking up", object.name, "at floor", e.position)
                        if len(e.carrying) == e.capacity:
                            break   # when capacity is reached, stop checking if there are passengers to pick up (break for loop)
            if DEL:
                awaiting = [p for ind, p in enumerate(awaiting) if ind not in DEL] #remove dropped passengers from awaiting list

        # decide if to reverse
        if len(e.carrying) == 0: #if the elevator isn't carrying any passengers
            reverse = 1 #reverse direction unless
            for object in awaiting: #there are passengers to pick up in the current direction
                if ((object.origin - e.position) > 0) == e.direction:
                    reverse = 0
                    break
            if reverse == 1:
                e.reverse()

        # if there's a passenger waiting in the same direction, move one floor; if not, keep the position and re-evaluate
        if len(e.carrying) > 0 or reverse == 0:
            e.move()

        # break in case of infinite loop
        if e.movement > 10000: break

    # calculate the total cost
    total_cost = 0
    for _, object in enumerate(b.passengers):
        print(object.name, "going from floor", object.origin, "to floor", object.destination,"have a cost of", object.cost)
        total_cost += object.cost
    print("The total cost is", total_cost)

###########################################################################


#Strategy 2:
# Elevator goes all the way up and then down and opens door at every floor
def strategy_2(b, e): #inputs a building and an elevator
    awaiting = copy.copy(b.passengers) #list of passengers in the building 
    e.carrying = [] #reset elevator
    while len(awaiting) > 0 or len(e.carrying) > 0: #while there are people to be picked up or people to deliver
        print("The elevator is at", e.position, "carrying", len(e.carrying), "passengers")

        # at each floor, first check if there is a passenger to drop
        e.drop_passenger()
        
        # if the elevator still has capacity, check if there is passenger to carry
        if len(awaiting) > 0 and len(e.carrying) < e.capacity:
            DEL = []
            for key, object in enumerate(awaiting): #loop through all waiting passengers in the building
                print(e.position, object.name, object.origin)
                if e.position == object.origin:
                    e.carrying.append(object) #pick up passenger
                    DEL.append(key) # add passenger to be removed from elevator calls
                    print("Picking up", object.name, "at floor", e.position)
                    if len(e.carrying) == e.capacity:
                        break   # when capacity is reached, stop checking if there are passengers to pick up (break for loop)
            if DEL:
                awaiting = [p for ind, p in enumerate(awaiting) if ind not in DEL] #remove dropped passengers from awaiting list

        # decide if to reverse
        if e.position == b.num_of_floor: #if at the top, go down
            e.direction = 0
        elif e.position == 0: #if on ground floor, go back up
            e.direction = 1
        
        #move elevator in up or down direction
        e.move()

        # break in case of infinite loop
        if e.movement > 100: break

    # calculate the total cost
    total_cost = 0
    for _, object in enumerate(b.passengers):
        print(object.name, "going from floor", object.origin, "to floor", object.destination,"have a cost of", object.cost)
        total_cost += object.cost
    print("The total cost is", total_cost)

###########################################################################

In [2]:
building_1 = Building(50, 25)
elevator_1 = Elevator(10)

strategy_1(copy.copy(building_1), copy.copy(elevator_1))
strategy_2(copy.copy(building_1), copy.copy(elevator_1))

The elevator is at 0 carrying 0 passengers
The elevator is at 1 carrying 0 passengers
Picking up Cznstf at floor 1
The elevator is at 2 carrying 1 passengers
The elevator is at 3 carrying 1 passengers
The elevator is at 4 carrying 1 passengers
Picking up Ufauht at floor 4
Picking up Husn at floor 4
The elevator is at 5 carrying 3 passengers
Picking up Tja at floor 5
The elevator is at 6 carrying 4 passengers
Picking up Dsiu at floor 6
The elevator is at 7 carrying 5 passengers
The elevator is at 8 carrying 5 passengers
Drop off Cznstf at floor 8 with cost 1
The elevator is at 9 carrying 4 passengers
Picking up Yzdlc at floor 9
Picking up Vqm at floor 9
The elevator is at 10 carrying 6 passengers
The elevator is at 11 carrying 6 passengers
Drop off Yzdlc at floor 11 with cost 9
The elevator is at 12 carrying 5 passengers
The elevator is at 13 carrying 5 passengers
The elevator is at 14 carrying 5 passengers
The elevator is at 15 carrying 5 passengers
Picking up Gkijabzf at floor 15
The 